# Segmenting and Clustering Neighborhoods in Toronto

## Part 1

Let's start by importing everything we will need

In [3]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt 

We can use the read_html function from pandas to obtain the content of the wiki site.

In [4]:
wiki = pd.read_html('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M', header=0)
wiki

[    Postal Code           Borough  \
 0           M1A      Not assigned   
 1           M2A      Not assigned   
 2           M3A        North York   
 3           M4A        North York   
 4           M5A  Downtown Toronto   
 ..          ...               ...   
 175         M5Z      Not assigned   
 176         M6Z      Not assigned   
 177         M7Z      Not assigned   
 178         M8Z         Etobicoke   
 179         M9Z      Not assigned   
 
                                          Neighbourhood  
 0                                         Not assigned  
 1                                         Not assigned  
 2                                            Parkwoods  
 3                                     Victoria Village  
 4                            Regent Park, Harbourfront  
 ..                                                 ...  
 175                                       Not assigned  
 176                                       Not assigned  
 177                

This returns a list of multple tables scraped from the wiki. We are only interessted in the first table

In [5]:
df=wiki[0]
df

Postal Code           Borough  \
0           M1A      Not assigned   
1           M2A      Not assigned   
2           M3A        North York   
3           M4A        North York   
4           M5A  Downtown Toronto   
..          ...               ...   
175         M5Z      Not assigned   
176         M6Z      Not assigned   
177         M7Z      Not assigned   
178         M8Z         Etobicoke   
179         M9Z      Not assigned   

                                         Neighbourhood  
0                                         Not assigned  
1                                         Not assigned  
2                                            Parkwoods  
3                                     Victoria Village  
4                            Regent Park, Harbourfront  
..                                                 ...  
175                                       Not assigned  
176                                       Not assigned  
177                                       Not assigned  
178  Mimico NW, The Queensway West, South of Bloor,...  
179                                       Not assigned  

[180 rows x 3 columns]

Let's drop all rows with "Not assigned" Borough. We do this by checking if the Borough Field contains "Not assigned", finding the inverse of the resulting boolean array with "~" and applying the resulting mask to our original dataframe.

In [6]:
df=df[~df['Borough'].str.contains('Not assigned')]
df.head(11)

Postal Code           Borough                                Neighbourhood
2          M3A        North York                                    Parkwoods
3          M4A        North York                             Victoria Village
4          M5A  Downtown Toronto                    Regent Park, Harbourfront
5          M6A        North York             Lawrence Manor, Lawrence Heights
6          M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government
8          M9A         Etobicoke      Islington Avenue, Humber Valley Village
9          M1B       Scarborough                               Malvern, Rouge
11         M3B        North York                                    Don Mills
12         M4B         East York              Parkview Hill, Woodbine Gardens
13         M5B  Downtown Toronto                     Garden District, Ryerson
14         M6B        North York                                    Glencairn

Let's check if we have any 'Not assigned' values in the Neighbourhood column.

In [7]:
df[df['Neighbourhood'].str.contains('Not assigned')]

Empty DataFrame
Columns: [Postal Code, Borough, Neighbourhood]
Index: []

This looks good! Now we use the shape method.

In [8]:
df.shape

(103, 3)

## End of Part 1 Beginning of Part 2

In [9]:
!pip install geocoder
import geocoder

     |████████████████████████████████| 98 kB 1.5 MB/s eta 0:00:011
     |████████████████████████████████| 829 kB 1.8 MB/s eta 0:00:01
     |████████████████████████████████| 82 kB 1.6 MB/s eta 0:00:01
  Created wheel for future: filename=future-0.18.2-py3-none-any.whl size=491058 sha256=68d4a70fa961e385bdc247dddd901247b8641af362381cf2270b83a240b85057
  Stored in directory: /home/tobias/.cache/pip/wheels/6e/9c/ed/4499c9865ac1002697793e0ae05ba6be33553d098f3347fb94
Successfully built future


The geocoder does not work for me so I will use the csv.

In [10]:
!wget -O coordinates.csv http://cocl.us/Geospatial_data
df_coord = pd.read_csv('coordinates.csv')
df_coord

--2020-08-12 11:04:05--  http://cocl.us/Geospatial_data
Resolving cocl.us (cocl.us)... 169.55.161.7
Connecting to cocl.us (cocl.us)|169.55.161.7|:80... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: https://cocl.us/Geospatial_data [following]
--2020-08-12 11:04:05--  https://cocl.us/Geospatial_data
Connecting to cocl.us (cocl.us)|169.55.161.7|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: https://ibm.box.com/shared/static/9afzr83pps4pwf2smjjcf1y5mvgb18rr.csv [following]
--2020-08-12 11:04:07--  https://ibm.box.com/shared/static/9afzr83pps4pwf2smjjcf1y5mvgb18rr.csv
Resolving ibm.box.com (ibm.box.com)... 185.235.236.197
Connecting to ibm.box.com (ibm.box.com)|185.235.236.197|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: /public/static/9afzr83pps4pwf2smjjcf1y5mvgb18rr.csv [following]
--2020-08-12 11:04:07--  https://ibm.box.com/public/static/9afzr83pps4pwf2smjjcf1y5

Postal Code   Latitude  Longitude
0           M1B  43.806686 -79.194353
1           M1C  43.784535 -79.160497
2           M1E  43.763573 -79.188711
3           M1G  43.770992 -79.216917
4           M1H  43.773136 -79.239476
..          ...        ...        ...
98          M9N  43.706876 -79.518188
99          M9P  43.696319 -79.532242
100         M9R  43.688905 -79.554724
101         M9V  43.739416 -79.588437
102         M9W  43.706748 -79.594054

[103 rows x 3 columns]

Now we need to merge the two dataframes. We use the merge functions so we can join on the Postal code column of the data frames

In [11]:
df2=pd.merge(df,df_coord, on='Postal Code')
df2

Postal Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M6A        North York   
4           M7A  Downtown Toronto   
..          ...               ...   
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                         Neighbourhood   Latitude  Longitude  
0                                            Parkwoods  43.753259 -79.329656  
1                                     Victoria Village  43.725882 -79.315572  
2                            Regent Park, Harbourfront  43.654260 -79.360636  
3                     Lawrence Manor, Lawrence Heights  43.718518 -79.464763  
4          Queen's Park, Ontario Provincial Government  43.662301 -79.389494  
..                                                 ...        ...        ...  
98       The Kingsway, Montgomery Road, Old Mill North  43.653654 -79.506944  
99                                Church and Wellesley  43.665860 -79.383160  
100  Business reply mail Processing Centre, South C...  43.662744 -79.321558  
101  Old Mill South, King's Mill Park, Sunnylea, Hu...  43.636258 -79.498509  
102  Mimico NW, The Queensway West, South of Bloor,...  43.628841 -79.520999  

[103 rows x 5 columns]

## End of Part 2, Beginning of Part 3

Let's have a look at the neighbourhoods on a map. First we install and import folium. We additionally need requests

In [12]:
!pip install folium
import folium
import requests

     |████████████████████████████████| 93 kB 1.3 MB/s eta 0:00:011


Second, we plot the neighbourhoods on the map and give the different boroughs different colors.

In [13]:
#longitude and latitude of toronto
lat=43.66135
long=-79.383087

map_toronto = folium.Map(location=[lat, long], zoom_start=10,control_scale = True)

#array with multiple colors
palette = ['blue', 'cadetblue', 'darkblue', 'darkgreen', 'darkpurple', 'darkred', 'gray', 'green', 'lightblue', 'lightgray', 'lightgreen', 'lightred', 'orange', 'pink', 'purple', 'red', 'white','beige','black']

for i,bor in enumerate(pd.unique(df['Borough'])):
    df3=df2[df2['Borough'].str.match(bor)]
    for lat, lng, neigh in zip(df3['Latitude'], df3['Longitude'], df3['Neighbourhood']):
        label = folium.Popup(neigh, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup="<b>"+ bor + "</b>: " + neigh,
            color=palette[i],
            fill=True,
            fill_color=palette[i],
            fill_opacity=1,
            parse_html=False).add_to(map_toronto)

map_toronto

For the third part of this assignment I would like to have a look at how the venues lokated in the different city parts and if they form spatial clusters, i.e. if there are parts of the city were we have a high venue density.

Therefore, we need to get the venues of every Neighbourhood. We do this in 4 steps, later we will put the last 3 steps in a loop.

**First step:**
Set the basic parameters for Foursquare:

I use the getpass library to keep my credentials secret.

In [14]:
import getpass
CLIENT_ID = getpass.getpass('ID:')
CLIENT_SECRET = getpass.getpass('SECRET:')
VERSION = '20180605' # Foursquare API version

ID:········
SECRET:········


**Second step:**
get all venues of a neighbourhood, in this example it is the neighbourhood with the index 3, which is Lawrence Manor, Lawrence Heights. Foursquare returns a maximum of 100 venues. Since the neighbourhoods in the city centre are closer together than the neighbourhoods in the suburbs we need an adaptive approach to get as many venues as possible. If our requeste returns a number of venues that is below 50 we will increase the radius and repeat the request. We start at a radius of 800. 

In [15]:
j=3
neighborhood_latitude = df2.loc[j, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = df2.loc[j, 'Longitude'] # neighborhood longitude value
name=df2.loc[j, 'Neighbourhood']
radius=800
LIMIT=100
nvenues=0
while nvenues<50:
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, neighborhood_latitude, neighborhood_longitude, VERSION, radius, LIMIT)
    results = requests.get(url).json()
    nvenues=len(results['response']['groups'][0]['items'])
    if (nvenues <50):
        radius=radius+300
        print(name+ ': '+str(nvenues) + ' venues found, radius increased to '+str(radius))
    else:
        print(name+ ': '+str(nvenues) + ' venues found')
        
items = results['response']['groups'][0]['items']
#items

Lawrence Manor, Lawrence Heights: 38 venues found, radius increased to 1100
Lawrence Manor, Lawrence Heights: 51 venues found


**Third step:** we convert the json file to a pd dataframe. In preparation of the next step we also convert the venue.location.formattedAddress field from an array to a string.

In [16]:
df_venue= pd.json_normalize(items)
df_venue['venue.location.formattedAddress']=df_venue['venue.location.formattedAddress'].apply(', '.join)
df_venue.head()

referralId  reasons.count  \
0  e-0-4b16e8b6f964a52051bf23e3-0              0   
1  e-0-4ccc5aebee23a14370591ea8-1              0   
2  e-0-4b12e300f964a520299023e3-2              0   
3  e-0-54c3d9ed498e50c810920ee4-3              0   
4  e-0-55fc4738498ea821b8d881ae-4              0   

                                       reasons.items  \
0  [{'summary': 'This spot is popular', 'type': '...   
1  [{'summary': 'This spot is popular', 'type': '...   
2  [{'summary': 'This spot is popular', 'type': '...   
3  [{'summary': 'This spot is popular', 'type': '...   
4  [{'summary': 'This spot is popular', 'type': '...   

                   venue.id                             venue.name  \
0  4b16e8b6f964a52051bf23e3                                  Roots   
1  4ccc5aebee23a14370591ea8         Lac Vien Vietnamese Restaurant   
2  4b12e300f964a520299023e3  Kitchen Stuff Plus (Clearance Outlet)   
3  54c3d9ed498e50c810920ee4                            BATLgrounds   
4  55fc4738498ea821b8d881ae                    The Burger's Priest   

            venue.location.address  venue.location.lat  venue.location.lng  \
0                 71-95 Orfus Road           43.718214          -79.463893   
1               141 Cartwright Ave           43.721259          -79.468472   
2                      76 Orfus Rd           43.719096          -79.462675   
3  153 Bridgeland Ave, Units 15-16           43.724054          -79.463398   
4                 3280 Dufferin St           43.720789          -79.456766   

                       venue.location.labeledLatLngs  venue.location.distance  \
0  [{'label': 'display', 'lat': 43.71821373389962...                       77   
1  [{'label': 'display', 'lat': 43.72125878799614...                      426   
2  [{'label': 'display', 'lat': 43.71909636823933...                      179   
3  [{'label': 'display', 'lat': 43.72405414025907...                      625   
4  [{'label': 'display', 'lat': 43.7207893797841,...                      691   

   ... venue.location.city venue.location.state venue.location.country  \
0  ...             Toronto                   ON                 Canada   
1  ...             Toronto                   ON                 Canada   
2  ...             Toronto                   ON                 Canada   
3  ...             Toronto                   ON                 Canada   
4  ...             Toronto                   ON                 Canada   

                     venue.location.formattedAddress  \
0       71-95 Orfus Road, Toronto ON M6A 1L9, Canada   
1             141 Cartwright Ave, Toronto ON, Canada   
2                    76 Orfus Rd, Toronto ON, Canada   
3  153 Bridgeland Ave, Units 15-16 (Dufferin St),...   
4       3280 Dufferin St, Toronto ON M6A 2T5, Canada   

                                    venue.categories venue.photos.count  \
0  [{'id': '4bf58dd8d48988d104951735', 'name': 'B...                  0   
1  [{'id': '4bf58dd8d48988d14a941735', 'name': 'V...                  0   
2  [{'id': '4bf58dd8d48988d1f8941735', 'name': 'F...                  0   
3  [{'id': '4f4528bc4b90abdf24c9de85', 'name': 'A...                  0   
4  [{'id': '4bf58dd8d48988d16e941735', 'name': 'F...                  0   

  venue.photos.groups  venue.venuePage.id venue.location.crossStreet  \
0                  []                 NaN                        NaN   
1                  []           137238575                        NaN   
2                  []                 NaN                        NaN   
3                  []                 NaN                Dufferin St   
4                  []                 NaN                        NaN   

  venue.location.neighborhood  
0                         NaN  
1                         NaN  
2                         NaN  
3                   Downsview  
4                         NaN  

[5 rows x 22 columns]

**Fourth step:** We drop every venue that does not have the right Postal Code for the recent request

In [17]:
df_venue=df_venue[df_venue['venue.location.formattedAddress'].str.contains(df2.loc[j,'Postal Code'])]
df_venue.head()

referralId  reasons.count  \
0  e-0-4b16e8b6f964a52051bf23e3-0              0   
3  e-0-54c3d9ed498e50c810920ee4-3              0   
4  e-0-55fc4738498ea821b8d881ae-4              0   
5  e-0-4b5f1f11f964a52047a729e3-5              0   
7  e-0-5ae3d754d3cce8002c86cbe1-7              0   

                                       reasons.items  \
0  [{'summary': 'This spot is popular', 'type': '...   
3  [{'summary': 'This spot is popular', 'type': '...   
4  [{'summary': 'This spot is popular', 'type': '...   
5  [{'summary': 'This spot is popular', 'type': '...   
7  [{'summary': 'This spot is popular', 'type': '...   

                   venue.id                venue.name  \
0  4b16e8b6f964a52051bf23e3                     Roots   
3  54c3d9ed498e50c810920ee4               BATLgrounds   
4  55fc4738498ea821b8d881ae       The Burger's Priest   
5  4b5f1f11f964a52047a729e3  Yuki Japanese Restaurant   
7  5ae3d754d3cce8002c86cbe1         RH Courtyard Café   

            venue.location.address  venue.location.lat  venue.location.lng  \
0                 71-95 Orfus Road           43.718214          -79.463893   
3  153 Bridgeland Ave, Units 15-16           43.724054          -79.463398   
4                 3280 Dufferin St           43.720789          -79.456766   
5                3259 Dufferin St.           43.720610          -79.456119   
7             3401 Dufferin Street           43.724874          -79.455536   

                       venue.location.labeledLatLngs  venue.location.distance  \
0  [{'label': 'display', 'lat': 43.71821373389962...                       77   
3  [{'label': 'display', 'lat': 43.72405414025907...                      625   
4  [{'label': 'display', 'lat': 43.7207893797841,...                      691   
5  [{'label': 'display', 'lat': 43.72060971477955...                      733   
7  [{'label': 'display', 'lat': 43.7248736, 'lng'...                     1025   

   ... venue.location.city venue.location.state venue.location.country  \
0  ...             Toronto                   ON                 Canada   
3  ...             Toronto                   ON                 Canada   
4  ...             Toronto                   ON                 Canada   
5  ...             Toronto                   ON                 Canada   
7  ...             Toronto                   ON                 Canada   

                     venue.location.formattedAddress  \
0       71-95 Orfus Road, Toronto ON M6A 1L9, Canada   
3  153 Bridgeland Ave, Units 15-16 (Dufferin St),...   
4       3280 Dufferin St, Toronto ON M6A 2T5, Canada   
5      3259 Dufferin St., Toronto ON M6A 2T2, Canada   
7   3401 Dufferin Street, Toronto ON M6A 2T9, Canada   

                                    venue.categories venue.photos.count  \
0  [{'id': '4bf58dd8d48988d104951735', 'name': 'B...                  0   
3  [{'id': '4f4528bc4b90abdf24c9de85', 'name': 'A...                  0   
4  [{'id': '4bf58dd8d48988d16e941735', 'name': 'F...                  0   
5  [{'id': '4bf58dd8d48988d1d2941735', 'name': 'S...                  0   
7  [{'id': '4bf58dd8d48988d1c4941735', 'name': 'R...                  0   

  venue.photos.groups  venue.venuePage.id venue.location.crossStreet  \
0                  []                 NaN                        NaN   
3                  []                 NaN                Dufferin St   
4                  []                 NaN                        NaN   
5                  []                 NaN                        NaN   
7                  []                 NaN                        NaN   

  venue.location.neighborhood  
0                         NaN  
3                   Downsview  
4                         NaN  
5                         NaN  
7                         NaN  

[5 rows x 22 columns]

Let's put step 2-4 in a loop and use this loop to get the venues for all the neighbourhoods.

In [19]:
df_venues_neigh=pd.DataFrame()#columns=['referralId','reasons.count','reasons.items','venue.id','venue.name','venue.location.address','venue.location.crossStreet','venue.location.lat','venue.location.lng','venue.location.labeledLatLngs','...','venue.location.cc','venue.location.city','venue.location.state','venue.location.country','venue.location.formattedAddress','venue.categories','venue.photos.count','venue.photos.groups','venue.location.neighborhood','venue.venuePage.id'])
for j in range(len(df2)):
    neighborhood_latitude = df2.loc[j, 'Latitude'] # neighborhood latitude value
    neighborhood_longitude = df2.loc[j, 'Longitude'] # neighborhood longitude value
    name=df2.loc[j, 'Neighbourhood']
    radius=800
    LIMIT=100
    nvenues=0
    while nvenues<50:
        url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, neighborhood_latitude, neighborhood_longitude, VERSION, radius, LIMIT)
        results = requests.get(url).json()
        nvenues=len(results['response']['groups'][0]['items'])
        if (nvenues <50):
            radius=radius+500
            print(name+ ': '+str(nvenues) + ' venues found, radius increased to '+str(radius))
        else:
            print(name+ ': '+str(nvenues) + ' venues found')
    items = results['response']['groups'][0]['items']
    df_venue= pd.json_normalize(items)
    df_venue['venue.location.formattedAddress']=df_venue['venue.location.formattedAddress'].apply(', '.join)
    df_venue=df_venue[df_venue['venue.location.formattedAddress'].str.contains(df2.loc[j,'Postal Code'])]
    df_venues_neigh=df_venues_neigh.append(df_venue)
df_venues_neigh

Parkwoods: 5 venues found, radius increased to 1300
Parkwoods: 34 venues found, radius increased to 1800
Parkwoods: 88 venues found
Victoria Village: 6 venues found, radius increased to 1300
Victoria Village: 37 venues found, radius increased to 1800
Victoria Village: 70 venues found
Regent Park, Harbourfront: 80 venues found
Lawrence Manor, Lawrence Heights: 38 venues found, radius increased to 1300
Lawrence Manor, Lawrence Heights: 92 venues found
Queen's Park, Ontario Provincial Government: 100 venues found
Islington Avenue, Humber Valley Village: 10 venues found, radius increased to 1300
Islington Avenue, Humber Valley Village: 21 venues found, radius increased to 1800
Islington Avenue, Humber Valley Village: 41 venues found, radius increased to 2300
Islington Avenue, Humber Valley Village: 57 venues found
Malvern, Rouge: 10 venues found, radius increased to 1300
Malvern, Rouge: 24 venues found, radius increased to 1800
Malvern, Rouge: 38 venues found, radius increased to 2300
Malv

Downsview: 24 venues found, radius increased to 1800
Downsview: 51 venues found
Studio District: 100 venues found
Bedford Park, Lawrence Manor East: 39 venues found, radius increased to 1300
Bedford Park, Lawrence Manor East: 86 venues found
Del Ray, Mount Dennis, Keelsdale and Silverthorn: 11 venues found, radius increased to 1300
Del Ray, Mount Dennis, Keelsdale and Silverthorn: 46 venues found, radius increased to 1800
Del Ray, Mount Dennis, Keelsdale and Silverthorn: 42 venues found, radius increased to 2300
Del Ray, Mount Dennis, Keelsdale and Silverthorn: 100 venues found
Humberlea, Emery: 7 venues found, radius increased to 1300
Humberlea, Emery: 11 venues found, radius increased to 1800
Humberlea, Emery: 41 venues found, radius increased to 2300
Humberlea, Emery: 58 venues found
Birch Cliff, Cliffside West: 8 venues found, radius increased to 1300
Birch Cliff, Cliffside West: 13 venues found, radius increased to 1800
Birch Cliff, Cliffside West: 29 venues found, radius increase

referralId  reasons.count  \
0    e-0-4b8991cbf964a520814232e3-0              0   
2    e-0-4bd4846a6798ef3bd0c5618d-2              0   
5    e-0-4b8ec91af964a520053733e3-5              0   
6    e-0-57e286f2498e43d84d92d34a-6              0   
16  e-0-58a8dcaa6119f47b9a94dc05-16              0   
..                              ...            ...   
72  e-0-4d0408907d9ba35d83856323-72              0   
74  e-0-4b0703f6f964a52080f522e3-74              0   
77  e-0-4be5bc1d2457a593d3eaab15-77              0   
79  e-0-4eda7c9e77c8274efd426dad-79              0   
81  e-0-50cf7872e4b08217676abc90-81              0   

                                        reasons.items  \
0   [{'summary': 'This spot is popular', 'type': '...   
2   [{'summary': 'This spot is popular', 'type': '...   
5   [{'summary': 'This spot is popular', 'type': '...   
6   [{'summary': 'This spot is popular', 'type': '...   
16  [{'summary': 'This spot is popular', 'type': '...   
..                                                ...   
72  [{'summary': 'This spot is popular', 'type': '...   
74  [{'summary': 'This spot is popular', 'type': '...   
77  [{'summary': 'This spot is popular', 'type': '...   
79  [{'summary': 'This spot is popular', 'type': '...   
81  [{'summary': 'This spot is popular', 'type': '...   

                    venue.id                   venue.name  \
0   4b8991cbf964a520814232e3              Allwyn's Bakery   
2   4bd4846a6798ef3bd0c5618d  Donalda Golf & Country Club   
5   4b8ec91af964a520053733e3           Graydon Hall Manor   
6   57e286f2498e43d84d92d34a                  Tim Hortons   
16  58a8dcaa6119f47b9a94dc05                          A&W   
..                       ...                          ...   
72  4d0408907d9ba35d83856323   King's Garden Banquet Hall   
74  4b0703f6f964a52080f522e3               ShaSha Organic   
77  4be5bc1d2457a593d3eaab15                  Fogh Marine   
79  4eda7c9e77c8274efd426dad              Krown Etobicoke   
81  50cf7872e4b08217676abc90            Costco Food Court   

      venue.location.address  venue.location.lat  venue.location.lng  \
0         81 Underhill drive           43.759840          -79.324719   
2             12 Bushbury Dr           43.752816          -79.342741   
5     185 Graydon Hall Drive           43.763923          -79.342961   
6             215 Brookbanks           43.760668          -79.326368   
16      1277 York Mills Road           43.760643          -79.326865   
..                       ...                 ...                 ...   
72        15 Canmotor Avenue           43.622929          -79.510698   
74           20 Plastics Ave           43.623370          -79.509302   
77             901 Oxford St           43.619122          -79.514810   
79        1401 The Queensway           43.619759          -79.530293   
81  50 Queen Elizabeth Blvd.           43.622727          -79.507455   

                        venue.location.labeledLatLngs  \
0   [{'label': 'display', 'lat': 43.75984035203157...   
2   [{'label': 'display', 'lat': 43.75281596740471...   
5   [{'label': 'display', 'lat': 43.76392256055678...   
6   [{'label': 'display', 'lat': 43.76066827030228...   
16  [{'label': 'display', 'lat': 43.76064307616131...   
..                                                ...   
72  [{'label': 'display', 'lat': 43.6229291, 'lng'...   
74  [{'label': 'display', 'lat': 43.62337, 'lng': ...   
77  [{'label': 'display', 'lat': 43.61912207338791...   
79  [{'label': 'display', 'lat': 43.619759, 'lng':...   
81  [{'label': 'display', 'lat': 43.62272689757317...   

    venue.location.distance  ... venue.location.state venue.location.country  \
0                       833  ...                   ON                 Canada   
2                      1053  ...                   ON                 Canada   
5                      1597  ...                   ON                 Canada   
6                       866  ...                   ON                 Canada   
16      

We used a significant amount of the 950 requests we can send, so let's copy the data we obtained into an other Dataframe we will work with and save the obtained data into a csv so we don't have to get it again.

In [20]:
df_venues2=df_venues_neigh.reset_index()
df_venues2.to_csv('Venues.csv')

We would like to display all of the venues on the map with the marker-cluster-plugin of folium.

In [21]:
import folium.plugins as fplugins
lat=43.66135
long=-79.383087

map_toronto2 = folium.Map(location=[lat, long], zoom_start=10,control_scale = True)

# instantiate a mark cluster object
venues_cluster = fplugins.MarkerCluster().add_to(map_toronto2)

# loop through the dataframe and add each data point to the mark cluster
for lat, lng, label, in zip(df_venues2['venue.location.lat'], df_venues2['venue.location.lng'],df_venues2['venue.name']):
    folium.Marker(
        location=[lat, lng],
        icon=None,
        popup=label,
    ).add_to(venues_cluster)

# display map
map_toronto2

As we can see, the largest ammount of venues seem to be found in downtown. Let's use a more scientific clustering method to cluster the spatial data of the locations. We will use the density-based clustering algorithm DBSCAN from the sklearn library.

In [24]:
from sklearn.cluster import DBSCAN

ClusterData = df_venues2[['venue.location.lat','venue.location.lng']]
db = DBSCAN(eps=0.005, min_samples=20).fit(ClusterData)
labels = db.labels_
unique_labels = set(labels)
print(unique_labels)
df_venues2['cluster_label']=labels
df_venues2.head()

{0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, -1}


index                       referralId  reasons.count  \
0      0   e-0-4b8991cbf964a520814232e3-0              0   
1      2   e-0-4bd4846a6798ef3bd0c5618d-2              0   
2      5   e-0-4b8ec91af964a520053733e3-5              0   
3      6   e-0-57e286f2498e43d84d92d34a-6              0   
4     16  e-0-58a8dcaa6119f47b9a94dc05-16              0   

                                       reasons.items  \
0  [{'summary': 'This spot is popular', 'type': '...   
1  [{'summary': 'This spot is popular', 'type': '...   
2  [{'summary': 'This spot is popular', 'type': '...   
3  [{'summary': 'This spot is popular', 'type': '...   
4  [{'summary': 'This spot is popular', 'type': '...   

                   venue.id                   venue.name  \
0  4b8991cbf964a520814232e3              Allwyn's Bakery   
1  4bd4846a6798ef3bd0c5618d  Donalda Golf & Country Club   
2  4b8ec91af964a520053733e3           Graydon Hall Manor   
3  57e286f2498e43d84d92d34a                  Tim Hortons   
4  58a8dcaa6119f47b9a94dc05                          A&W   

   venue.location.address  venue.location.lat  venue.location.lng  \
0      81 Underhill drive           43.759840          -79.324719   
1          12 Bushbury Dr           43.752816          -79.342741   
2  185 Graydon Hall Drive           43.763923          -79.342961   
3          215 Brookbanks           43.760668          -79.326368   
4    1277 York Mills Road           43.760643          -79.326865   

                       venue.location.labeledLatLngs  ...  \
0  [{'label': 'display', 'lat': 43.75984035203157...  ...   
1  [{'label': 'display', 'lat': 43.75281596740471...  ...   
2  [{'label': 'display', 'lat': 43.76392256055678...  ...   
3  [{'label': 'display', 'lat': 43.76066827030228...  ...   
4  [{'label': 'display', 'lat': 43.76064307616131...  ...   

   venue.location.country                    venue.location.formattedAddress  \
0                  Canada     81 Underhill drive, Toronto ON M3A 1Z5, Canada   
1                  Canada       12 Bushbury Dr, Don Mills ON M3A 2Z7, Canada   
2                  Canada  185 Graydon Hall Drive, Toronto ON M3A 3B4, Ca...   
3                  Canada  215 Brookbanks (York Miils Rd), Toronto ON M3A...   
4                  Canada   1277 York Mills Road, Toronto ON M3A 1Z5, Canada   

                                    venue.categories venue.photos.count  \
0  [{'id': '4bf58dd8d48988d144941735', 'name': 'C...                  0   
1  [{'id': '4bf58dd8d48988d1e6941735', 'name': 'G...                  0   
2  [{'id': '4bf58dd8d48988d171941735', 'name': 'E...                  0   
3  [{'id': '4bf58dd8d48988d16d941735', 'name': 'C...                  0   
4  [{'id': '4bf58dd8d48988d16e941735', 'name': 'F...                  0   

  venue.photos.groups venue.location.crossStreet venue.venuePage.id  \
0                  []                        NaN                NaN   
1                  []                        NaN                NaN   
2                  []                        NaN           52496423   
3                  []              York Miils Rd                NaN   
4                  []                        NaN                NaN   

  venue.events.count venue.events.summary  cluster_label  
0                NaN                  NaN             -1  
1                NaN                  NaN             -1  
2                NaN                  NaN             -1  
3                NaN                  NaN             -1  
4                NaN                  NaN             -1  

[5 rows x 26 columns]

Let's have a look at our spatial venue clusters.

In [25]:
palette = ['blue', 'cadetblue', 'darkblue', 'darkgreen', 'darkpurple', 'darkred', 'gray', 'green', 'lightblue', 'lightgray', 'lightgreen', 'lightred', 'orange', 'pink', 'purple', 'red', 'white','beige','black','blue', 'cadetblue', 'darkblue', 'darkgreen', 'darkpurple', 'darkred', 'gray', 'green', 'lightblue', 'lightgray', 'lightgreen', 'lightred', 'orange', 'pink', 'purple', 'red', 'white','beige','black','blue', 'cadetblue', 'darkblue', 'darkgreen', 'darkpurple', 'darkred', 'gray', 'green', 'lightblue', 'lightgray', 'lightgreen', 'lightred', 'orange', 'pink', 'purple', 'red', 'white','beige','black']

map_toronto3 = folium.Map(location=[lat, long], zoom_start=11,control_scale = True)
for i in range(0,len(unique_labels)-1):
    df_venues3=df_venues2[df_venues2['cluster_label']==i]
    for lat, lng, name, in zip(df_venues3['venue.location.lat'], df_venues3['venue.location.lng'],df_venues3['venue.name']):
        label = folium.Popup(name, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=name,
            color=palette[i],
            fill=True,
            fill_color=palette[i],
            fill_opacity=1,
            parse_html=False).add_to(map_toronto3)

map_toronto3


As we expected, the largest venue cluster is in Downtown Toronto (blue). Other clusters include main streets, e.g. Avenue Road (white markers) and St.Clair Avenue West (brown markers); Malls, e.g. Bayview Village (orange markers) and Yorkdale Shopping Centre (cadetblue markers); and central places in the suburbs, e.g. the North York Centre (beige markers).